# 1. Import bibliotek

In [52]:
import pandas as pd
from ydata_profiling import ProfileReport
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.preprocessing import StandardScaler
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.pipeline import Pipeline
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_score
from sklearn.metrics import balanced_accuracy_score
from sklearn.metrics import f1_score

from sklearn.decomposition import PCA
import joblib

# 2. Załadowanie danych
## - załadowanie i wyświetlenie zbioru
About Dataset
This dataset is a cleaned version of Pulsar Classification For Class Prediction Dataset. Different techniques like outlier removal, z-score normalization, and feature selection have been used for creating this dataset.
It contains 8 columns:

Mean_Integrated: Mean of Observations
EK: Excess kurtosis of Observations
Skewness: It's a measure of the asymmetry of the probability distribution of a real-valued random variable about its mean. It refers to the skewness of Observations
Mean _ DMSNR _ Curve: Mean of DM SNR CURVE of Observation
SD _ DMSNR _ Curve: Standard deviation of DM SNR CURVE of Observations
EK _ DMSNR _ Curve: Excess kurtosis of DM SNR CURVE of Observations
Skewness _ DMSNR _ Curve: Skewness of DM SNR CURVE of Observations
Class: Binary (either 0 or 1)
Explanation:
Radio waves emitted from pulsars reach Earth after traveling long distances in space that is filled with free electrons. The important point is that pulsars emit a wide range of frequencies and the amount which which the electrons slow down the wave depends on the frequency. Waves with higher frequency are sowed down less as compared with waves with higher frequency. It means dispersion.

In [53]:
data = pd.DataFrame(pd.read_csv('Pulsar_cleaned.csv'))
data

Mean_Integrated        EK  Skewness  Mean_DMSNR_Curve  SD_DMSNR_Curve  \
0           140.562500  1.502969 -0.699648          3.199833       19.110426   
1           102.507812  0.788423 -0.515088          1.677258       14.860146   
2           103.015625  0.323558  1.051164          3.121237       21.744669   
3           136.750000  0.958983 -0.636238          3.642977       20.959280   
4            88.726562  1.232198  1.123492          1.178930       11.468720   
...                ...       ...       ...               ...             ...   
14982        96.000000  0.537495  0.281344          1.871237       15.833746   
14983       136.429688  1.349991 -0.738123          1.296823       12.166062   
14984       122.554688  0.316006  0.323061         16.409699       44.626893   
14985       119.335938  0.213253 -0.743025         21.430602       58.872000   
14986       114.507812  0.076409 -0.024789          1.946488       13.381731   

       EK_DMSNR_Curve  Skewness_DMSNR_Curve  Class  
0            7.975532             74.242225      0  
1           10.576487            127.393580      0  
2            7.735822             63.171909      0  
3            6.896499             53.593661      0  
4           14.269573            252.567306      0  
...               ...                   ...    ...  
14982        9.634927            104.821623      0  
14983       15.450260            285.931022      0  
14984        2.945244              8.297092      0  
14985        2.499517              4.595173      0  
14986       10.007967            134.238910      0  

[14987 rows x 8 columns]

# 3. Sprawdzenie czy są braki w danych

In [54]:
data.isna().any()

Mean_Integrated         False
EK                      False
Skewness                False
Mean_DMSNR_Curve        False
SD_DMSNR_Curve          False
EK_DMSNR_Curve          False
Skewness_DMSNR_Curve    False
Class                   False
dtype: bool

# 4. Analiza eksporacyjna danych przy wykorzystaniu Pandas profiling

In [55]:
profile = ProfileReport(data, title="Profiling Report")
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Wnioski z analizy ekspolarcyjnych danych

- Dane są niezbalansowane ~85% to dane z klasą 0, a klasę 1 reprezentuje ~15% 
- Brak brakujących danych
- wysoka korelacja 6 kolumn z tego powodu użyję metody PCA 


## 5. Podział danych metodą warstwową ze względu na niezbalansowanie kolumny class

In [56]:
#kolumny z danymi
X = data.iloc[:,:-1]

#wybranie klasy z etykietami
y = data.iloc[:,-1]

#podzial danych metodą warstwową, ponieważ dane są niezbalansowane
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, train_size=0.8, random_state=42, shuffle=True,stratify=y)

## 6. Budowa potoku do przetwarzania danych złożonego z:
- skalowanie
- wykorzystanie algorytmu PCA, ponieważ występują dane o wysokiej korelacji
- na podstawie testów dużo szybciej działał model KNN oraz wskaźniki modelu byly najlepsze. Porównawczo wykorzystałem model w tym samym schemacie pracy RandomForestClassifier, SVM, lecz pracowaly dłużej i przedstawiał gorsze rezultaty

In [57]:
# Budowa potoku przetwarzania: skalowanie + klasyfikator KNN
pipeline = Pipeline([
    ('scaler', StandardScaler()),
    ('pca', PCA()),  
    ('knn', KNeighborsClassifier())
])

## 7. Wykorzystanie pakietu Grid Search do znalezienia optymalnych parametrów modelu KNN

In [58]:
#Parametry do przeszukiwania w Grid Search
parameters = {
    'pca__n_components': [1, 2, 3 ,4 ,5 ,6 ,7],
    'knn__n_neighbors': [1, 3, 5 ,7 ,9],
    'knn__weights': ['uniform', 'distance'],
    'knn__algorithm': ['auto', 'ball_tree', 'kd_tree', 'brute']
}

In [59]:
#Dostrojenie modelu
grid_search = GridSearchCV(pipeline, parameters, cv=5, verbose=1, n_jobs=-1)

## 8. Stworzenie modelu

In [60]:
#zapis modelu do zmiennej
model = grid_search.fit(X_train, y_train)

#wyświetlenie optymalnych parametrów
grid_search.best_params_

Fitting 5 folds for each of 280 candidates, totalling 1400 fits


{'knn__algorithm': 'auto',
 'knn__n_neighbors': 7,
 'knn__weights': 'uniform',
 'pca__n_components': 5}

## 9. Wykonanie predykcji

In [61]:
y_pred = model.predict(X_test)

## 10. Raport klasyfikacji

In [62]:
print(classification_report(y_test, y_pred))
print(confusion_matrix(y_test, y_pred))
print('accuracy_score',accuracy_score(y_test, y_pred))
print('precision_score',precision_score(y_test, y_pred))
print('balanced_accuracy_score',balanced_accuracy_score(y_test, y_pred))
print('f1_score', f1_score(y_test, y_pred))

              precision    recall  f1-score   support

           0       0.99      1.00      0.99      2936
           1       0.88      0.45      0.60        62

    accuracy                           0.99      2998
   macro avg       0.93      0.73      0.79      2998
weighted avg       0.99      0.99      0.99      2998

[[2932    4]
 [  34   28]]
accuracy_score 0.9873248832555037
precision_score 0.875
balanced_accuracy_score 0.7251252527028215
f1_score 0.5957446808510638


## 11. Zapis modelu

In [63]:
joblib.dump(model, 'knn_model.pkl')

['knn_model.pkl']

## 12. Wnioski
- Dane były niezbalansowane co wpłyneło na osiągane wyniki. Z tego powodu wynik accuracy_score należalo uzupełnić dodatkowymi wskaźnikami
- Wysoki wskaźnik dokładności i precyzji wskazuje na dobre klasyfikowanie danych negatywnych przypadków
- Niższe wskaźniki recall, f1_score wskazują, że model ma problemy z identyfikacją wszystkich pozytywnych przypadków (recall 0.45) i klasyfikuje je jako fałszywie negatywne 
